USAR KERNEL 3.10.11

In [1]:
import pandas as pd
import numpy as np
from tabulate import tabulate
ordenes= pd.read_csv("./Historicos_Ordenes.csv")
caracteristicas= pd.read_csv("./Caracteristicas_Equipos.csv")
registros= pd.read_csv("./Registros_Condiciones.csv")


REGISTROS

In [2]:
registros.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9000 entries, 0 to 8999
Data columns (total 6 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   ID_Registro       9000 non-null   int64  
 1   ID_Equipo         9000 non-null   int64  
 2   Fecha             9000 non-null   object 
 3   Temperatura_C     9000 non-null   float64
 4   Vibracion_mm_s    9000 non-null   float64
 5   Horas_Operativas  8960 non-null   float64
dtypes: float64(3), int64(2), object(1)
memory usage: 422.0+ KB


In [3]:
registros["Fecha"]=pd.to_datetime(registros["Fecha"])

CONTEO DE VALORES NULOS

In [4]:
registros.isna().sum()

ID_Registro          0
ID_Equipo            0
Fecha                0
Temperatura_C        0
Vibracion_mm_s       0
Horas_Operativas    40
dtype: int64

ELIMINO 40 VALORES NULOS

In [4]:
registros.dropna(inplace=True)
registros.info()

<class 'pandas.core.frame.DataFrame'>
Index: 8960 entries, 0 to 8999
Data columns (total 6 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   ID_Registro       8960 non-null   int64         
 1   ID_Equipo         8960 non-null   int64         
 2   Fecha             8960 non-null   datetime64[ns]
 3   Temperatura_C     8960 non-null   float64       
 4   Vibracion_mm_s    8960 non-null   float64       
 5   Horas_Operativas  8960 non-null   float64       
dtypes: datetime64[ns](1), float64(3), int64(2)
memory usage: 490.0 KB


Busqueda de duplicados

In [5]:
registros[registros.duplicated()]

Empty DataFrame
Columns: [ID_Registro, ID_Equipo, Fecha, Temperatura_C, Vibracion_mm_s, Horas_Operativas]
Index: []

VALORES ATIPICOS

In [6]:
z_scores = (registros.select_dtypes(include=[np.number])-registros.select_dtypes(include=[np.number]).mean(numeric_only=True))/registros.select_dtypes(include=[np.number]).std(numeric_only=True)
z_scores_abs = z_scores.apply(np.abs)
#print(tabulate(z_scores_abs, headers='keys'))
umbral = 3
out_mask = ~z_scores[z_scores_abs > umbral].isna()
print(out_mask.sum())
outliers = registros['Temperatura_C'][out_mask['Temperatura_C']]
outliers

ID_Registro          0
ID_Equipo            0
Temperatura_C       30
Vibracion_mm_s       0
Horas_Operativas     0
dtype: int64


255     999.0
300     999.0
476     999.0
824     999.0
1719    999.0
1979    999.0
2121    999.0
2399    999.0
2444    999.0
2592    999.0
2638    999.0
2654    999.0
2995    999.0
3625    999.0
4173    999.0
5035    999.0
5066    999.0
5077    999.0
5156    999.0
6016    999.0
6389    999.0
7416    999.0
7465    999.0
7651    999.0
7870    999.0
8092    999.0
8249    999.0
8300    999.0
8893    999.0
8895    999.0
Name: Temperatura_C, dtype: float64

BORRO LOS 30 OUTLIERS

In [7]:
registros.drop(outliers.index,inplace=True)
registros.info()

<class 'pandas.core.frame.DataFrame'>
Index: 8930 entries, 0 to 8999
Data columns (total 6 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   ID_Registro       8930 non-null   int64         
 1   ID_Equipo         8930 non-null   int64         
 2   Fecha             8930 non-null   datetime64[ns]
 3   Temperatura_C     8930 non-null   float64       
 4   Vibracion_mm_s    8930 non-null   float64       
 5   Horas_Operativas  8930 non-null   float64       
dtypes: datetime64[ns](1), float64(3), int64(2)
memory usage: 488.4 KB


CARDINALIDAD

In [8]:
def calc_cardinalidad(adf):
    result = {}
    for col in adf.columns:
        print('\n- Valores únicos para "{0}"'.format(col), '\n')
        # print(adf[col].unique())
        card = len(adf[col].unique())
        print('Num valores únicos: ', len(adf[col].unique()))
        result[col] = card
    return result
registros_card = calc_cardinalidad(registros)
print(registros_card)


- Valores únicos para "ID_Registro" 

Num valores únicos:  8930

- Valores únicos para "ID_Equipo" 

Num valores únicos:  499

- Valores únicos para "Fecha" 

Num valores únicos:  8930

- Valores únicos para "Temperatura_C" 

Num valores únicos:  5896

- Valores únicos para "Vibracion_mm_s" 

Num valores únicos:  491

- Valores únicos para "Horas_Operativas" 

Num valores únicos:  8518
{'ID_Registro': 8930, 'ID_Equipo': 499, 'Fecha': 8930, 'Temperatura_C': 5896, 'Vibracion_mm_s': 491, 'Horas_Operativas': 8518}


In [9]:
for col in registros.columns:
    print('frecuencia para: "{0}"'.format(col),"\n")
    print(registros[col].value_counts())

frecuencia para: "ID_Registro" 

ID_Registro
1       1
5999    1
5993    1
5994    1
5995    1
       ..
2998    1
2997    1
2995    1
2994    1
9000    1
Name: count, Length: 8930, dtype: int64
frecuencia para: "ID_Equipo" 

ID_Equipo
202    34
155    32
32     30
475    30
229    30
       ..
142    10
371    10
318     9
114     8
399     7
Name: count, Length: 499, dtype: int64
frecuencia para: "Fecha" 

Fecha
2020-01-01 00:00:00    1
2020-09-06 22:00:00    1
2020-09-06 16:00:00    1
2020-09-06 17:00:00    1
2020-09-06 18:00:00    1
                      ..
2020-05-04 21:00:00    1
2020-05-04 20:00:00    1
2020-05-04 18:00:00    1
2020-05-04 17:00:00    1
2021-01-09 23:00:00    1
Name: count, Length: 8930, dtype: int64
frecuencia para: "Temperatura_C" 

Temperatura_C
96.00     6
64.88     6
104.24    6
87.71     6
83.46     6
         ..
141.61    1
142.85    1
80.45     1
52.49     1
127.40    1
Name: count, Length: 5896, dtype: int64
frecuencia para: "Vibracion_mm_s" 

Vibracion_

ANALISIS DE CORRELACION

In [10]:
registros.corr(method="pearson",numeric_only=True)

ID_Registro  ID_Equipo  Temperatura_C  Vibracion_mm_s  \
ID_Registro          1.000000  -0.000848       0.008495       -0.002676   
ID_Equipo           -0.000848   1.000000       0.011234       -0.002396   
Temperatura_C        0.008495   0.011234       1.000000       -0.008729   
Vibracion_mm_s      -0.002676  -0.002396      -0.008729        1.000000   
Horas_Operativas    -0.001860   0.007966      -0.013577       -0.003300   

                  Horas_Operativas  
ID_Registro              -0.001860  
ID_Equipo                 0.007966  
Temperatura_C            -0.013577  
Vibracion_mm_s           -0.003300  
Horas_Operativas          1.000000

ANALISIS SESGO

In [11]:
registros_skw=registros.skew(numeric_only=True)
registros_skw

ID_Registro         0.000246
ID_Equipo           0.036998
Temperatura_C       0.009538
Vibracion_mm_s      0.007265
Horas_Operativas   -0.024799
dtype: float64

KURTOSIS

In [12]:
registros_kurt = registros.kurt(numeric_only=True)
registros_kurt

ID_Registro        -1.198987
ID_Equipo          -1.196854
Temperatura_C      -1.198364
Vibracion_mm_s     -1.185016
Horas_Operativas   -1.212018
dtype: float64

PROFILING

In [ ]:
#! pip install ydata-profiling


In [13]:
from ydata_profiling import ProfileReport
profile = ProfileReport(registros, title="Sales Profiling Report")
profile.to_notebook_iframe()
profile.to_file('sales_profile_report.html')


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

/anaconda/envs/azureml_py38/lib/python3.10/site-packages/ydata_profiling/profile_report.py:358: UserWarning: Try running command: 'pip install --upgrade Pillow' to avoid ValueError
  warnings.warn(


Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

###ORDENES


In [14]:
ordenes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10020 entries, 0 to 10019
Data columns (total 7 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   ID_Orden             10020 non-null  int64  
 1   ID_Equipo            10020 non-null  int64  
 2   Fecha                10020 non-null  object 
 3   Tipo_Mantenimiento   10020 non-null  object 
 4   Costo_Mantenimiento  9970 non-null   float64
 5   Duracion_Horas       10020 non-null  int64  
 6   Ubicacion            10020 non-null  object 
dtypes: float64(1), int64(3), object(3)
memory usage: 548.1+ KB


In [15]:
ordenes["Fecha"]=pd.to_datetime(ordenes["Fecha"])

CONTEO DE VALORES NULOS

In [16]:
ordenes.isna().sum()

ID_Orden                0
ID_Equipo               0
Fecha                   0
Tipo_Mantenimiento      0
Costo_Mantenimiento    50
Duracion_Horas          0
Ubicacion               0
dtype: int64

ELIMINO 50 VALORES NULOS

In [17]:
ordenes.dropna(inplace=True)

BUSQUEDDA DE DUPLICADOS

In [18]:
ordenes[ordenes.duplicated()]

ID_Orden  ID_Equipo               Fecha Tipo_Mantenimiento  \
10000         1        465 2020-01-01 00:00:00         Correctivo   
10001         2        418 2020-01-01 01:00:00         Correctivo   
10002         3        228 2020-01-01 02:00:00         Correctivo   
10003         4        300 2020-01-01 03:00:00         Correctivo   
10004         5        325 2020-01-01 04:00:00         Correctivo   
10005         6        449 2020-01-01 05:00:00         Preventivo   
10006         7        234 2020-01-01 06:00:00         Preventivo   
10007         8        487 2020-01-01 07:00:00         Correctivo   
10008         9        191 2020-01-01 08:00:00         Correctivo   
10009        10        444 2020-01-01 09:00:00         Preventivo   
10010        11        335 2020-01-01 10:00:00         Correctivo   
10011        12         86 2020-01-01 11:00:00         Correctivo   
10012        13        275 2020-01-01 12:00:00         Correctivo   
10013        14        161 2020-01-01 13:00:00         Correctivo   
10014        15         81 2020-01-01 14:00:00         Correctivo   
10015        16        323 2020-01-01 15:00:00         Correctivo   
10016        17        245 2020-01-01 16:00:00         Correctivo   
10017        18        235 2020-01-01 17:00:00         Preventivo   
10018        19         60 2020-01-01 18:00:00         Correctivo   
10019        20        288 2020-01-01 19:00:00         Preventivo   

       Costo_Mantenimiento  Duracion_Horas     Ubicacion  
10000              1405.20              47  Planta Norte  
10001              5922.92              38  Planta Norte  
10002              7119.05              34  Planta Oeste  
10003              3488.33              38  Planta Oeste  
10004              5611.37              15   Planta Este  
10005              7996.45              32  Planta Norte  
10006              8648.28               5   Planta Este  
10007              2329.24               6    Planta Sur  
10008              1743.03              33   Planta Este  
10009              8899.57              30  Planta Norte  
10010              2993.12              38  Planta Oeste  
10011              7790.27              32  Planta Oeste  
10012              5323.28               3  Planta Norte  
10013              4986.48              17  Planta Oeste  
10014              7579.60              30   Planta Este  
10015              6776.04              23    Planta Sur  
10016              1809.27              32   Planta Este  
10017              2335.50              34    Planta Sur  
10018              7485.46              30   Planta Este  
10019              4010.69              37   Planta Este

BORRADO DE 20 DUPLICADOS

In [19]:
ordenes.drop_duplicates(inplace=True)

VALORES ATIPICOS

In [23]:
z_scores = (ordenes.select_dtypes(include=[np.number])-ordenes.select_dtypes(include=[np.number]).mean(numeric_only=True))/ordenes.select_dtypes(include=[np.number]).std(numeric_only=True)
z_scores_abs = z_scores.apply(np.abs)
#print(tabulate(z_scores_abs, headers='keys'))
umbral = 3
out_mask = ~z_scores[z_scores_abs > umbral].isna()
print(out_mask.sum())



ID_Orden               0
ID_Equipo              0
Costo_Mantenimiento    0
Duracion_Horas         0
dtype: int64


CARDINALIDAD

In [24]:
def calc_cardinalidad(adf):
    result = {}
    for col in adf.columns:
        print('\n- Valores únicos para "{0}"'.format(col), '\n')
        # print(adf[col].unique())
        card = len(adf[col].unique())
        print('Num valores únicos: ', len(adf[col].unique()))
        result[col] = card
    return result
ordenes_card = calc_cardinalidad(ordenes)
print(ordenes_card)


- Valores únicos para "ID_Orden" 

Num valores únicos:  9950

- Valores únicos para "ID_Equipo" 

Num valores únicos:  499

- Valores únicos para "Fecha" 

Num valores únicos:  9950

- Valores únicos para "Tipo_Mantenimiento" 

Num valores únicos:  2

- Valores únicos para "Costo_Mantenimiento" 

Num valores únicos:  9888

- Valores únicos para "Duracion_Horas" 

Num valores únicos:  47

- Valores únicos para "Ubicacion" 

Num valores únicos:  4
{'ID_Orden': 9950, 'ID_Equipo': 499, 'Fecha': 9950, 'Tipo_Mantenimiento': 2, 'Costo_Mantenimiento': 9888, 'Duracion_Horas': 47, 'Ubicacion': 4}


In [25]:
for col in ordenes.columns:
    print('frecuencia para: "{0}"'.format(col),"\n")
    print(ordenes[col].value_counts())

frecuencia para: "ID_Orden" 

ID_Orden
1        1
6670     1
6663     1
6664     1
6665     1
        ..
3335     1
3336     1
3337     1
3338     1
10000    1
Name: count, Length: 9950, dtype: int64
frecuencia para: "ID_Equipo" 

ID_Equipo
172    36
488    34
141    33
130    32
443    32
       ..
7      11
192    10
227     9
176     8
242     7
Name: count, Length: 499, dtype: int64
frecuencia para: "Fecha" 

Fecha
2020-01-01 00:00:00    1
2020-10-04 21:00:00    1
2020-10-04 14:00:00    1
2020-10-04 15:00:00    1
2020-10-04 16:00:00    1
                      ..
2020-05-18 22:00:00    1
2020-05-18 23:00:00    1
2020-05-19 00:00:00    1
2020-05-19 01:00:00    1
2021-02-20 15:00:00    1
Name: count, Length: 9950, dtype: int64
frecuencia para: "Tipo_Mantenimiento" 

Tipo_Mantenimiento
Correctivo    5059
Preventivo    4891
Name: count, dtype: int64
frecuencia para: "Costo_Mantenimiento" 

Costo_Mantenimiento
5010.91    2
3429.95    2
548.36     2
4401.80    2
4100.72    2
          ..


ANALISIS DE CORRELACION

In [26]:
ordenes.corr(method="pearson",numeric_only=True)

ID_Orden  ID_Equipo  Costo_Mantenimiento  Duracion_Horas
ID_Orden             1.000000  -0.012955             0.017253       -0.003095
ID_Equipo           -0.012955   1.000000             0.003275       -0.010754
Costo_Mantenimiento  0.017253   0.003275             1.000000        0.003282
Duracion_Horas      -0.003095  -0.010754             0.003282        1.000000

ANALISIS SESGO

In [27]:
ordenes_skw=ordenes.skew(numeric_only=True)
ordenes_skw

ID_Orden              -0.000204
ID_Equipo             -0.004636
Costo_Mantenimiento    0.032017
Duracion_Horas        -0.009935
dtype: float64

KURTOSIS

In [28]:
ordenes_kurt = ordenes.kurt(numeric_only=True)
ordenes_kurt

ID_Orden              -1.199871
ID_Equipo             -1.216803
Costo_Mantenimiento   -1.198569
Duracion_Horas        -1.192842
dtype: float64

PROFILING

In [29]:
from ydata_profiling import ProfileReport
profile = ProfileReport(ordenes, title="Sales Profiling Report")
profile.to_notebook_iframe()
profile.to_file('sales_profile_report.html')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

/anaconda/envs/azureml_py38/lib/python3.10/site-packages/ydata_profiling/profile_report.py:358: UserWarning: Try running command: 'pip install --upgrade Pillow' to avoid ValueError
  warnings.warn(


Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

CARACTERISTICAS

In [30]:
caracteristicas.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 505 entries, 0 to 504
Data columns (total 6 columns):
 #   Column                       Non-Null Count  Dtype 
---  ------                       --------------  ----- 
 0   ID_Equipo                    505 non-null    int64 
 1   Tipo_Equipo                  505 non-null    object
 2   Fabricante                   505 non-null    object
 3   Modelo                       505 non-null    object
 4   Potencia_kW                  505 non-null    int64 
 5   Horas_Recomendadas_Revision  505 non-null    int64 
dtypes: int64(3), object(3)
memory usage: 23.8+ KB


CONTEO DE VALORES NULOS

In [31]:
caracteristicas.isna().sum()

ID_Equipo                      0
Tipo_Equipo                    0
Fabricante                     0
Modelo                         0
Potencia_kW                    0
Horas_Recomendadas_Revision    0
dtype: int64

BUSQUEDDA DE DUPLICADOS

In [32]:
caracteristicas[caracteristicas.duplicated()]

ID_Equipo    Tipo_Equipo Fabricante Modelo  Potencia_kW  \
500          1          Motor  Schneider   X100         1009   
501          2          Motor        ABB   Z300         1220   
502          3          Motor         GE   Y200         3733   
503          4  Transformador    Siemens   X100          662   
504          5      Compresor        ABB   Y200          982   

     Horas_Recomendadas_Revision  
500                         9656  
501                         2165  
502                         6674  
503                         1480  
504                         4282

BORRADO DE 5 DUPLICADOS

In [33]:
caracteristicas.drop_duplicates(inplace=True)

VALORES ATIPICOS

In [34]:
z_scores = (caracteristicas-caracteristicas.mean(numeric_only=True))/caracteristicas.std(numeric_only=True)
z_scores_abs = z_scores.apply(np.abs)
#print(tabulate(z_scores_abs, headers='keys'))
umbral = 3
out_mask = ~z_scores[z_scores_abs > umbral].isna()
print(out_mask.sum())

Fabricante                     0
Horas_Recomendadas_Revision    0
ID_Equipo                      0
Modelo                         0
Potencia_kW                    0
Tipo_Equipo                    0
dtype: int64


CARDINALIDAD

In [35]:
def calc_cardinalidad(adf):
    result = {}
    for col in adf.columns:
        print('\n- Valores únicos para "{0}"'.format(col), '\n')
        # print(adf[col].unique())
        card = len(adf[col].unique())
        print('Num valores únicos: ', len(adf[col].unique()))
        result[col] = card
    return result
caracteristicas_card = calc_cardinalidad(caracteristicas)
print(caracteristicas_card)


- Valores únicos para "ID_Equipo" 

Num valores únicos:  500

- Valores únicos para "Tipo_Equipo" 

Num valores únicos:  4

- Valores únicos para "Fabricante" 

Num valores únicos:  4

- Valores únicos para "Modelo" 

Num valores únicos:  4

- Valores únicos para "Potencia_kW" 

Num valores únicos:  471

- Valores únicos para "Horas_Recomendadas_Revision" 

Num valores únicos:  490
{'ID_Equipo': 500, 'Tipo_Equipo': 4, 'Fabricante': 4, 'Modelo': 4, 'Potencia_kW': 471, 'Horas_Recomendadas_Revision': 490}


In [36]:
for col in caracteristicas.columns:
    print('frecuencia para: "{0}"'.format(col),"\n")
    print(caracteristicas[col].value_counts())

frecuencia para: "ID_Equipo" 

ID_Equipo
1      1
330    1
343    1
342    1
341    1
      ..
162    1
161    1
160    1
159    1
500    1
Name: count, Length: 500, dtype: int64
frecuencia para: "Tipo_Equipo" 

Tipo_Equipo
Generador        135
Transformador    126
Compresor        121
Motor            118
Name: count, dtype: int64
frecuencia para: "Fabricante" 

Fabricante
ABB          131
Siemens      129
GE           124
Schneider    116
Name: count, dtype: int64
frecuencia para: "Modelo" 

Modelo
Z300    141
Y200    126
X100    122
M400    111
Name: count, dtype: int64
frecuencia para: "Potencia_kW" 

Potencia_kW
-100     10
 562      3
 3527     2
 1536     2
 670      2
         ..
 1881     1
 1521     1
 3546     1
 4560     1
 877      1
Name: count, Length: 471, dtype: int64
frecuencia para: "Horas_Recomendadas_Revision" 

Horas_Recomendadas_Revision
655     2
6992    2
2270    2
8101    2
2386    2
       ..
4360    1
5036    1
1315    1
1443    1
5082    1
Name: count, Leng

ANALISIS DE CORRELACION

In [37]:
caracteristicas.corr(method="pearson",numeric_only=True)

ID_Equipo  Potencia_kW  \
ID_Equipo                     1.000000     0.004271   
Potencia_kW                   0.004271     1.000000   
Horas_Recomendadas_Revision   0.013656     0.083409   

                             Horas_Recomendadas_Revision  
ID_Equipo                                       0.013656  
Potencia_kW                                     0.083409  
Horas_Recomendadas_Revision                     1.000000

ANALISIS SESGO

In [38]:
caracteristicas_skw=caracteristicas.skew(numeric_only=True)
caracteristicas_skw

ID_Equipo                      0.000000
Potencia_kW                    0.056597
Horas_Recomendadas_Revision   -0.029009
dtype: float64

KURTOSIS

In [39]:
caracteristicas_kurt = caracteristicas.kurt(numeric_only=True)
caracteristicas_kurt

ID_Equipo                     -1.200000
Potencia_kW                   -1.100520
Horas_Recomendadas_Revision   -1.152395
dtype: float64

PROFILING

In [40]:
from ydata_profiling import ProfileReport
profile = ProfileReport(caracteristicas, title="Sales Profiling Report")
profile.to_notebook_iframe()
profile.to_file('sales_profile_report.html')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

/anaconda/envs/azureml_py38/lib/python3.10/site-packages/ydata_profiling/profile_report.py:358: UserWarning: Try running command: 'pip install --upgrade Pillow' to avoid ValueError
  warnings.warn(


Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Frecuencia de mantenimiento: Número de mantenimientos realizados por equipo

In [41]:
ordenes.groupby("ID_Equipo").agg(num=("ID_Orden","count")).sort_values("num",ascending=False)

num
ID_Equipo     
172         36
488         34
141         33
443         32
130         32
...        ...
7           11
192         10
227          9
176          8
242          7

[499 rows x 1 columns]

Vida útil estimada: Estimación de la vida útil de los equipos basada en las horas operativas.

In [42]:
horas_recom_rev=caracteristicas[["ID_Equipo","Horas_Recomendadas_Revision"]]
horas_recom_rev

ID_Equipo  Horas_Recomendadas_Revision
0            1                         9656
1            2                         2165
2            3                         6674
3            4                         1480
4            5                         4282
..         ...                          ...
495        496                         5594
496        497                         8614
497        498                         5874
498        499                         6907
499        500                         5082

[500 rows x 2 columns]

In [43]:
latest_records = registros.loc[registros.groupby('ID_Equipo')['Fecha'].idxmax()]
horas_acumuladas=latest_records[["ID_Equipo","Horas_Operativas"]]
horas_acumuladas


ID_Equipo  Horas_Operativas
8350          1            5503.0
8666          2           48939.0
8228          3           68525.0
8571          4           87502.0
8798          5           41650.0
...         ...               ...
8804        495           42321.0
8304        496           71007.0
8552        497           49741.0
8293        498           70036.0
6556        499           82396.0

[499 rows x 2 columns]

In [140]:
comparacion_horas=pd.merge(horas_acumuladas,horas_recom_rev, on="ID_Equipo")
comparacion_horas['horas desde ult rev'] = comparacion_horas['Horas_Operativas'] % comparacion_horas['Horas_Recomendadas_Revision']
comparacion_horas['horas hasta la prox rev']=comparacion_horas['Horas_Recomendadas_Revision']-comparacion_horas['horas desde ult rev']
horas_hasta_prox_rev=comparacion_horas.sort_values(by="horas hasta la prox rev",ascending=True)
horas_hasta_prox_rev

ID_Equipo  Horas_Operativas  Horas_Recomendadas_Revision  \
190        191            2098.0                         2102   
63          64           96776.0                         6453   
326        327            7652.0                         3836   
430        431           78536.0                         7142   
484        485           13957.0                         6992   
..         ...               ...                          ...   
315        316           84194.0                         9290   
383        384           21045.0                         9921   
481        482           47845.0                         9429   
45          46           98817.0                         9788   
483        484           85776.0                         9528   

     horas desde ult rev  horas hasta la prox rev  
190               2098.0                      4.0  
63                6434.0                     19.0  
326               3816.0                     20.0  
430               7116.0                     26.0  
484               6965.0                     27.0  
..                   ...                      ...  
315                584.0                   8706.0  
383               1203.0                   8718.0  
481                700.0                   8729.0  
45                 937.0                   8851.0  
483                 24.0                   9504.0  

[499 rows x 5 columns]


Análisis Exploratorio de Datos con Python
Objetivo: Analizar las relaciones entre las características de los equipos, el historial de órdenes de trabajo y las condiciones operativas.
Tareas:
Realizar un análisis descriptivo de los datos:
Estadísticas básicas como la media, mediana y desviación estándar de las horas operativas, el costo de mantenimiento, y la frecuencia de fallos.
Detectar outliers en las columnas clave (por ejemplo, en Costo_Mantenimiento y Horas_Operativas).
Analizar la distribución de fallos y tipos de mantenimiento (correctivo/preventivo) de los equipos.
Establecer posibles correlaciones entre las variables, como la relación entre las condiciones operativas (temperatura, vibración) y las horas de operación.
Recomendación: Usar técnicas como groupby(), corr(), visualización de histogramas y diagramas de dispersión para detectar patrones y correlaciones.




Estadísticas básicas como la media, mediana y desviación estándar de las horas operativas, el costo de mantenimiento, y la frecuencia de fallos.

HORAS OPERATIVAS

In [82]:
media=horas_acumuladas[["Horas_Operativas"]].mean()
desviacion=horas_acumuladas[["Horas_Operativas"]].std()
mediana=horas_acumuladas[["Horas_Operativas"]].median()
print(f"Media: {media}")
print(f"Desviación Estándar: {desviacion}")
print(f"Mediana: {mediana}")

Media: Horas_Operativas    49843.470942
dtype: float64
Desviación Estándar: Horas_Operativas    29028.200443
dtype: float64
Mediana: Horas_Operativas    49563.0
dtype: float64


COSTE DE MANTENIMIENTO

In [99]:
media=ordenes[["Costo_Mantenimiento"]].mean()
desviacion=ordenes[["Costo_Mantenimiento"]].std()
mediana=ordenes[["Costo_Mantenimiento"]].median()
print("El coste de mantenimiento TOTAL:")
print(f"Media: {media}")
print(f"Desviación Estándar: {desviacion}")
print(f"Mediana: {mediana}")

El coste de mantenimiento TOTAL:
Media: Costo_Mantenimiento    4977.342366
dtype: float64
Desviación Estándar: Costo_Mantenimiento    2837.233565
dtype: float64
Mediana: Costo_Mantenimiento    4916.675
dtype: float64


In [91]:
coste_mto = ordenes[['ID_Equipo',"Costo_Mantenimiento"]].groupby('ID_Equipo').agg(MEDIA=("Costo_Mantenimiento","mean"), MEDIANA=("Costo_Mantenimiento","median"),DESVIACION_STD=("Costo_Mantenimiento","std")).sort_values("MEDIA",ascending=False)
print("El coste de mantenimiento por equipo:")
coste_mto

El coste de mantenimiento por equipo:


MEDIA   MEDIANA  DESVIACION_STD
ID_Equipo                                       
254        6956.170000  7415.920     2431.751225
299        6790.311667  7767.675     2075.448978
78         6658.467857  6965.445     2168.349573
423        6602.345000  6586.395     2116.637018
242        6513.377143  8114.200     3135.895175
...                ...       ...             ...
447        3527.959600  3458.400     2439.415354
330        3385.696000  1991.310     2920.991691
205        3356.644000  3175.450     2274.641135
58         2783.970667  1839.910     1950.361630
314        2498.380667  2094.520     1781.407520

[499 rows x 3 columns]

FRECUENCIA DE FALLOS (2 VERTIENTES NUMERO DE FALLOS Y DIAS ENTRE FALLOS CONSECUTIVOS)

In [137]:
frecuencia_fallos = ordenes[ordenes['Tipo_Mantenimiento'] == 'Correctivo'].groupby('ID_Equipo').size().reset_index(name='Numero_Fallos')
frecuencia_fallos
media=frecuencia_fallos[["Numero_Fallos"]].mean()
desviacion=frecuencia_fallos[["Numero_Fallos"]].std()
mediana=frecuencia_fallos[["Numero_Fallos"]].median()
print("Numero de fallos por equipo:")
print(f"Media: {media}")
print(f"Desviación Estándar: {desviacion}")
print(f"Mediana: {mediana}")
numero_fallos=frecuencia_fallos.sort_values("Numero_Fallos",ascending=False,ignore_index=True)
numero_fallos

Numero de fallos por equipo:
Media: Numero_Fallos    10.138277
dtype: float64
Desviación Estándar: Numero_Fallos    3.260897
dtype: float64
Mediana: Numero_Fallos    10.0
dtype: float64


ID_Equipo  Numero_Fallos
0          172             21
1          281             20
2           59             20
3          443             19
4           89             19
..         ...            ...
494        155              4
495        166              4
496        499              4
497         71              3
498         27              1

[499 rows x 2 columns]

In [135]:
ordenes_correctivo = ordenes[ordenes['Tipo_Mantenimiento'] == 'Correctivo']

# Calcular la diferencia de días entre cada orden de mantenimiento correctivo para cada equipo
ordenes_correctivo['Dias_Diferencia'] = ordenes_correctivo.groupby('ID_Equipo')['Fecha'].diff().dt.days
print("Numero de días entre fallos consecutivos")
dias_entre_fallos_consec=ordenes_correctivo[['ID_Equipo',"Dias_Diferencia"]].groupby('ID_Equipo').agg(MEDIA=("Dias_Diferencia","mean"), MEDIANA=("Dias_Diferencia","median"),DESVIACION_STD=("Dias_Diferencia","std")).sort_values("MEDIA",ascending=True)
dias_entre_fallos_consec

Numero de días entre fallos consecutivos


/tmp/ipykernel_6241/823061675.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ordenes_correctivo['Dias_Diferencia'] = ordenes_correctivo.groupby('ID_Equipo')['Fecha'].diff().dt.days


MEDIA  MEDIANA  DESVIACION_STD
ID_Equipo                                     
297         13.000000     12.0        7.549834
484         16.900000     12.0       18.002778
104         17.285714     13.0       15.274053
443         17.388889     10.0       19.079212
172         18.050000      6.0       21.047503
...               ...      ...             ...
242         89.500000     36.5      122.415958
124         91.000000     62.0      109.062673
260         94.750000     98.5       52.245414
481        108.333333    142.0       96.032980
27                NaN      NaN             NaN

[499 rows x 3 columns]

3. Mezcla y Combinación de Datos
Objetivo: Combinar los tres datasets en un único conjunto de datos que contenga toda la información relevante de cada equipo, las condiciones operativas y las órdenes de mantenimiento.

Tareas:

Merge: Utilizar la función merge() de pandas para combinar los tres datasets en un único dataframe. Las combinaciones deben realizarse a través de la columna ID_Equipo (o cualquier otro identificador único de equipo).

Asegurarse de que las columnas combinadas estén correctamente alineadas y que no haya valores nulos o duplicados tras la combinación.

Crear nuevas columnas combinadas que representen relaciones clave:

Tiempo hasta fallo: ¿Cuánto tiempo de operación transcurre hasta que un equipo requiere mantenimiento?
Relación entre condiciones operativas y fallos: ¿Cómo impactan la vibración o temperatura en la probabilidad de un fallo?
Recomendación: Usar pandas para realizar los joins o merges y la combinación de datasets, además de limpiar los datos resultantes para asegurarse de que no haya errores en los valores.

PARA ORDENES VOY A SACAR LA MEDIA DE COSTE Y LA MEDIA DE DURACION DE HORAS DE TODAS LAS ORDENES DE MANTENIMIENTO CORRECTIVO O PREVENTIVO DEL MISMO EQUIPO

In [186]:
ordenes_preventivo = ordenes[ordenes['Tipo_Mantenimiento'] == 'Preventivo']
ordenes_correctivo = ordenes[ordenes['Tipo_Mantenimiento'] == 'Correctivo']
ordenes_preventivo_agg=ordenes_preventivo[['ID_Equipo',"Costo_Mantenimiento","Duracion_Horas"]].groupby('ID_Equipo').agg(COSTE_MTO_PREV=("Costo_Mantenimiento","mean"), DURACION_HORAS_PREV=("Duracion_Horas","mean"))
ordenes_correctivo_agg=ordenes_correctivo[['ID_Equipo',"Costo_Mantenimiento","Duracion_Horas"]].groupby('ID_Equipo').agg(COSTE_MTO_CORR=("Costo_Mantenimiento","mean"), DURACION_HORAS_CORR=("Duracion_Horas","mean"))
ordenes_correctivo_agg


COSTE_MTO_CORR  DURACION_HORAS_CORR
ID_Equipo                                     
1             5284.873000            15.400000
2             3268.534286            16.857143
3             2923.602000            12.800000
4             6895.782500            23.500000
5             4787.365000            24.400000
...                   ...                  ...
495           5908.390833            21.583333
496           5850.827000            29.300000
497           4997.465455            21.272727
498           5395.426000            24.600000
499           5156.390000            33.250000

[499 rows x 2 columns]

In [187]:
COSTE_ORDENES=pd.merge(ordenes_correctivo_agg,ordenes_preventivo_agg, on="ID_Equipo")
COSTE_ORDENES

COSTE_MTO_CORR  DURACION_HORAS_CORR  COSTE_MTO_PREV  \
ID_Equipo                                                        
1             5284.873000            15.400000     4448.922000   
2             3268.534286            16.857143     4062.376667   
3             2923.602000            12.800000     5017.603333   
4             6895.782500            23.500000     4553.522500   
5             4787.365000            24.400000     4909.548571   
...                   ...                  ...             ...   
495           5908.390833            21.583333     3985.039091   
496           5850.827000            29.300000     5001.808182   
497           4997.465455            21.272727     4917.139091   
498           5395.426000            24.600000     5679.830909   
499           5156.390000            33.250000     5076.350909   

           DURACION_HORAS_PREV  
ID_Equipo                       
1                    28.000000  
2                    29.666667  
3                    20.833333  
4                    22.125000  
5                    19.714286  
...                        ...  
495                  26.636364  
496                  16.454545  
497                  26.636364  
498                  22.545455  
499                  31.181818  

[499 rows x 4 columns]

PARA CARACTERISTICAS NO VOY A HACER NADA PORQUE HAY UNA LINEA POR CADA EQUIPO

In [189]:
caracteristicas

ID_Equipo    Tipo_Equipo Fabricante Modelo  Potencia_kW  \
0            1          Motor  Schneider   X100         1009   
1            2          Motor        ABB   Z300         1220   
2            3          Motor         GE   Y200         3733   
3            4  Transformador    Siemens   X100          662   
4            5      Compresor        ABB   Y200          982   
..         ...            ...        ...    ...          ...   
495        496          Motor    Siemens   X100         3617   
496        497      Generador  Schneider   Y200          548   
497        498          Motor  Schneider   M400         2602   
498        499          Motor        ABB   M400          877   
499        500  Transformador         GE   X100         2039   

     Horas_Recomendadas_Revision  
0                           9656  
1                           2165  
2                           6674  
3                           1480  
4                           4282  
..                           ...  
495                         5594  
496                         8614  
497                         5874  
498                         6907  
499                         5082  

[500 rows x 6 columns]

In [191]:
AUX1=pd.merge(COSTE_ORDENES,caracteristicas, on="ID_Equipo")
AUX1

ID_Equipo  COSTE_MTO_CORR  DURACION_HORAS_CORR  COSTE_MTO_PREV  \
0            1     5284.873000            15.400000     4448.922000   
1            2     3268.534286            16.857143     4062.376667   
2            3     2923.602000            12.800000     5017.603333   
3            4     6895.782500            23.500000     4553.522500   
4            5     4787.365000            24.400000     4909.548571   
..         ...             ...                  ...             ...   
494        495     5908.390833            21.583333     3985.039091   
495        496     5850.827000            29.300000     5001.808182   
496        497     4997.465455            21.272727     4917.139091   
497        498     5395.426000            24.600000     5679.830909   
498        499     5156.390000            33.250000     5076.350909   

     DURACION_HORAS_PREV    Tipo_Equipo Fabricante Modelo  Potencia_kW  \
0              28.000000          Motor  Schneider   X100         1009   
1              29.666667          Motor        ABB   Z300         1220   
2              20.833333          Motor         GE   Y200         3733   
3              22.125000  Transformador    Siemens   X100          662   
4              19.714286      Compresor        ABB   Y200          982   
..                   ...            ...        ...    ...          ...   
494            26.636364      Compresor  Schneider   Y200         4383   
495            16.454545          Motor    Siemens   X100         3617   
496            26.636364      Generador  Schneider   Y200          548   
497            22.545455          Motor  Schneider   M400         2602   
498            31.181818          Motor        ABB   M400          877   

     Horas_Recomendadas_Revision  
0                           9656  
1                           2165  
2                           6674  
3                           1480  
4                           4282  
..                           ...  
494                         6188  
495                         5594  
496                         8614  
497                         5874  
498                         6907  

[499 rows x 10 columns]

PARA REGISTROS VOY A SACAR LA MEDIA DE TEMPERATURAS Y VIBRACIONES POR EQUIPO, EL VALOR DE LAS HORAS OPERATIVAS Y EL VALOR DE LAS HORAS HASTA PROX REVISION

In [153]:
medias_vib_temp = registros[['ID_Equipo',"Temperatura_C","Vibracion_mm_s"]].groupby('ID_Equipo').agg(MEDIA_TEMP=("Temperatura_C","mean"), MEDIA_VIBR=("Vibracion_mm_s","median"))
medias_vib_temp

MEDIA_TEMP  MEDIA_VIBR
ID_Equipo                        
1          106.908125       2.475
2           95.310000       2.370
3           93.922778       3.995
4           90.881500       2.410
5          107.714643       3.120
...               ...         ...
495        105.388947       2.280
496         91.598750       2.770
497        114.621053       2.210
498        100.603333       2.950
499         95.410000       3.040

[499 rows x 2 columns]

In [177]:
HORAS_HASTA_PROX_REV=horas_hasta_prox_rev[["ID_Equipo","Horas_Operativas","horas hasta la prox rev"]]
HORAS_HASTA_PROX_REV

ID_Equipo  Horas_Operativas  horas hasta la prox rev
190        191            2098.0                      4.0
63          64           96776.0                     19.0
326        327            7652.0                     20.0
430        431           78536.0                     26.0
484        485           13957.0                     27.0
..         ...               ...                      ...
315        316           84194.0                   8706.0
383        384           21045.0                   8718.0
481        482           47845.0                   8729.0
45          46           98817.0                   8851.0
483        484           85776.0                   9504.0

[499 rows x 3 columns]

In [193]:
AUX2=pd.merge(medias_vib_temp,HORAS_HASTA_PROX_REV, on="ID_Equipo")
AUX2

ID_Equipo  MEDIA_TEMP  MEDIA_VIBR  Horas_Operativas  \
0            1  106.908125       2.475            5503.0   
1            2   95.310000       2.370           48939.0   
2            3   93.922778       3.995           68525.0   
3            4   90.881500       2.410           87502.0   
4            5  107.714643       3.120           41650.0   
..         ...         ...         ...               ...   
494        495  105.388947       2.280           42321.0   
495        496   91.598750       2.770           71007.0   
496        497  114.621053       2.210           49741.0   
497        498  100.603333       2.950           70036.0   
498        499   95.410000       3.040           82396.0   

     horas hasta la prox rev  
0                     4153.0  
1                      856.0  
2                     4889.0  
3                     1298.0  
4                     1170.0  
..                       ...  
494                    995.0  
495                   1715.0  
496                   1943.0  
497                    452.0  
498                    488.0  

[499 rows x 5 columns]

VOY A AÑADIR INFORMACION YA EXTRAIDA COMO DIAS ENTRE FALLOS CONSECUTIVOS, NUMERO DE FALLOS, COSTE DE MTO TOTAL, HORAS HASTA LA PROXIMA REVISION

In [169]:
DIAS_ENTRE_FALL_CONSEC=dias_entre_fallos_consec[["MEDIA"]].rename(columns={"MEDIA":"DIAS_ENTRE_FALL_CONSEC"})
DIAS_ENTRE_FALL_CONSEC

DIAS_ENTRE_FALL_CONSEC
ID_Equipo                        
297                     13.000000
484                     16.900000
104                     17.285714
443                     17.388889
172                     18.050000
...                           ...
242                     89.500000
124                     91.000000
260                     94.750000
481                    108.333333
27                            NaN

[499 rows x 1 columns]

In [175]:
NUMERO_FALLOS=numero_fallos.set_index(['ID_Equipo'])
NUMERO_FALLOS


Numero_Fallos
ID_Equipo               
172                   21
281                   20
59                    20
443                   19
89                    19
...                  ...
155                    4
166                    4
499                    4
71                     3
27                     1

[499 rows x 1 columns]

In [194]:
AUX3=pd.merge(NUMERO_FALLOS,DIAS_ENTRE_FALL_CONSEC, on="ID_Equipo")
AUX3

Numero_Fallos  DIAS_ENTRE_FALL_CONSEC
ID_Equipo                                       
172                   21               18.050000
281                   20               20.263158
59                    20               20.789474
443                   19               17.388889
89                    19               20.722222
...                  ...                     ...
155                    4               46.000000
166                    4               87.666667
499                    4               88.333333
71                     3               81.000000
27                     1                     NaN

[499 rows x 2 columns]

In [168]:
COSTE_MTO_TOTAL=coste_mto[["MEDIA"]].rename(columns={"MEDIA":"COSTE_MTO_TOTAL"})

COSTE_MTO_TOTAL

COSTE_MTO_TOTAL
ID_Equipo                 
254            6956.170000
299            6790.311667
78             6658.467857
423            6602.345000
242            6513.377143
...                    ...
447            3527.959600
330            3385.696000
205            3356.644000
58             2783.970667
314            2498.380667

[499 rows x 1 columns]

In [195]:
AUX4=pd.merge(AUX3,COSTE_MTO_TOTAL, on="ID_Equipo")
AUX4

Numero_Fallos  DIAS_ENTRE_FALL_CONSEC  COSTE_MTO_TOTAL
ID_Equipo                                                        
172                   21               18.050000      4591.070556
281                   20               20.263158      5387.420667
59                    20               20.789474      5689.178966
443                   19               17.388889      5115.574062
89                    19               20.722222      4020.408519
...                  ...                     ...              ...
155                    4               46.000000      4659.689286
166                    4               87.666667      4769.095333
499                    4               88.333333      5097.694667
71                     3               81.000000      5713.180000
27                     1                     NaN      4953.803846

[499 rows x 3 columns]

In [196]:
AUX5=pd.merge(AUX4,AUX2, on="ID_Equipo")
AUX5

ID_Equipo  Numero_Fallos  DIAS_ENTRE_FALL_CONSEC  COSTE_MTO_TOTAL  \
0          172             21               18.050000      4591.070556   
1          281             20               20.263158      5387.420667   
2           59             20               20.789474      5689.178966   
3          443             19               17.388889      5115.574062   
4           89             19               20.722222      4020.408519   
..         ...            ...                     ...              ...   
494        155              4               46.000000      4659.689286   
495        166              4               87.666667      4769.095333   
496        499              4               88.333333      5097.694667   
497         71              3               81.000000      5713.180000   
498         27              1                     NaN      4953.803846   

     MEDIA_TEMP  MEDIA_VIBR  Horas_Operativas  horas hasta la prox rev  
0     94.746190       3.030           18119.0                   1363.0  
1     80.087000       1.305           17688.0                    300.0  
2    105.828750       2.720           93870.0                    378.0  
3     92.211667       3.180           93997.0                    268.0  
4    103.341875       2.435           24221.0                   5075.0  
..          ...         ...               ...                      ...  
494  102.045625       3.040            8873.0                    637.0  
495   89.302857       2.560           21832.0                   6700.0  
496   95.410000       3.040           82396.0                    488.0  
497   99.596250       3.465           79188.0                   2712.0  
498  103.502000       1.800           22143.0                   4323.0  

[499 rows x 8 columns]

In [197]:
AUX6=pd.merge(AUX5,AUX1, on="ID_Equipo")
AUX6

ID_Equipo  Numero_Fallos  DIAS_ENTRE_FALL_CONSEC  COSTE_MTO_TOTAL  \
0          172             21               18.050000      4591.070556   
1          281             20               20.263158      5387.420667   
2           59             20               20.789474      5689.178966   
3          443             19               17.388889      5115.574062   
4           89             19               20.722222      4020.408519   
..         ...            ...                     ...              ...   
494        155              4               46.000000      4659.689286   
495        166              4               87.666667      4769.095333   
496        499              4               88.333333      5097.694667   
497         71              3               81.000000      5713.180000   
498         27              1                     NaN      4953.803846   

     MEDIA_TEMP  MEDIA_VIBR  Horas_Operativas  horas hasta la prox rev  \
0     94.746190       3.030           18119.0                   1363.0   
1     80.087000       1.305           17688.0                    300.0   
2    105.828750       2.720           93870.0                    378.0   
3     92.211667       3.180           93997.0                    268.0   
4    103.341875       2.435           24221.0                   5075.0   
..          ...         ...               ...                      ...   
494  102.045625       3.040            8873.0                    637.0   
495   89.302857       2.560           21832.0                   6700.0   
496   95.410000       3.040           82396.0                    488.0   
497   99.596250       3.465           79188.0                   2712.0   
498  103.502000       1.800           22143.0                   4323.0   

     COSTE_MTO_CORR  DURACION_HORAS_CORR  COSTE_MTO_PREV  DURACION_HORAS_PREV  \
0       4723.289524            26.380952     4405.964000            17.066667   
1       5700.825000            20.000000     4760.612000            27.400000   
2       5653.631500            25.150000     5768.173333            23.222222   
3       5073.942632            29.052632     5176.420000            20.538462   
4       4120.192632            27.315789     3783.421250            22.250000   
..              ...                  ...             ...                  ...   
494     4343.627500            16.250000     4786.114000            24.900000   
495     3265.080000            20.250000     5316.010000            22.454545   
496     5156.390000            33.250000     5076.350909            31.181818   
497     5885.586667            38.000000     5670.078333            26.666667   
498     6095.010000            37.000000     4858.703333            34.250000   

       Tipo_Equipo Fabricante Modelo  Potencia_kW  Horas_Recomendadas_Revision  
0        Generador  Schneider   Z300         4194                         6494  
1        Compresor  Schneider   Y200         1625                         8994  
2        Generador  Schneider   M400         -100                         2244  
3    Transformador        ABB   X100         4078                         5545  
4        Generador         GE   M400          401                         7324  
..             ...        ...    ...          ...                          ...  
494      Generador         GE   Z300         4598                         1585  
495      Generador    Siemens   Y200         1521                         7133  
496          Motor        ABB   M400          877                         6907  
497      Compresor        ABB   X100         -100                         3150  
498      Compresor         GE   Z300         2431                         4411  

[499 rows x 17 columns]

In [ ]:
from ydata_profiling import ProfileReport
profile = ProfileReport(AUX6, title="REPORTE_TOTAL_DE MANTENIMIENTO")
profile.to_notebook_iframe()
profile.to_file('REPORTE_TOTAL_DE MANTENIMIENTO.html')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]